In [34]:
import numpy as np
import vtk
import pandas as pd
from vtk.util import numpy_support
from vtkmodules.vtkCommonCore import vtkPoints
from vtkmodules.vtkCommonDataModel import (
    vtkCellArray,
    vtkIterativeClosestPointTransform,
    vtkPolyData
)
from vtkmodules.vtkFiltersGeneral import vtkTransformPolyDataFilter
import sys
import warnings
import vtk.util.numpy_support as nps


In [3]:
def read_vtk_file(file_path):
    reader = vtk.vtkPolyDataReader()
    reader.SetFileName(file_path)
    reader.Update()
    return reader.GetOutput()

In [4]:
def generate_transformation_matrix(rotation_angle_deg, scale, translation):
    rotation_angle_rad = np.radians(rotation_angle_deg)
    R_z = np.array([
        [np.cos(rotation_angle_rad), -np.sin(rotation_angle_rad), 0],
        [np.sin(rotation_angle_rad), np.cos(rotation_angle_rad), 0],
        [0, 0, 1]
    ])
    R_z_scaled = scale * R_z
    transformation_matrix = np.eye(4)
    transformation_matrix[:3, :3] = R_z_scaled
    transformation_matrix[:3, 3] = translation
    return transformation_matrix

In [27]:
def numpy_points_to_vtk_polydata(numpyPoints):
    poly = vtk.vtkPolyData()
    points = vtk.vtkPoints()
    # We suppress a FutureWarning that involves an internal float/complex cast in numpy_to_vtk
    with warnings.catch_warnings():
        warnings.simplefilter("ignore")
        points.SetData(nps.numpy_to_vtk(numpyPoints))

    verts = vtk.vtkCellArray()
    for itervar in range(points.GetNumberOfPoints()):
        verts.InsertNextCell(1)
        verts.InsertCellPoint(itervar)

    poly.SetPoints(points)
    poly.SetVerts(verts)
    return poly


In [5]:
def apply_transformation_and_save(vtk_data, transformation_matrix, save_path, filename):
    vtk_transform = vtk.vtkTransform()
    vtk_matrix = vtk.vtkMatrix4x4()
    for i in range(4):
        for j in range(4):
            vtk_matrix.SetElement(i, j, transformation_matrix[i, j])
    vtk_transform.SetMatrix(vtk_matrix)

    transform_filter = vtk.vtkTransformPolyDataFilter()
    transform_filter.SetInputData(vtk_data)
    transform_filter.SetTransform(vtk_transform)
    transform_filter.Update()

    transformed_vtk_data = transform_filter.GetOutput()

    full_save_path = save_path + "/" + filename
    writer = vtk.vtkPolyDataWriter()
    writer.SetFileName(full_save_path)
    writer.SetInputData(transformed_vtk_data)
    writer.Write()
    print(f"Transformed data saved to {full_save_path}")
    return transformed_vtk_data

In [18]:
test_case = 1045
model_vtk_path = f"./out_poly_LF_{test_case}_cilynder.vtk"
Tinav_path = f"./rough-cylinder_{test_case}.vtk"
fine_points_path = f"./fine_cylinder_{test_case}.vtk"
save_path = "."

In [19]:
rotation_angle = 0  # 30 degrees rotation
scale = 1 # Uniform scaling factor
translation = np.array([0, 0, 0])  # Smaller translation vector
t_gold = generate_transformation_matrix(rotation_angle, scale, translation)
print(t_gold)

[[ 1. -0.  0.  0.]
 [ 0.  1.  0.  0.]
 [ 0.  0.  1.  0.]
 [ 0.  0.  0.  1.]]


In [20]:
model_vtk = read_vtk_file(model_vtk_path)

In [21]:
landmark_poly_data = read_vtk_file(Tinav_path)
vtk_points = landmark_poly_data.GetPoints()
landmark_points_array = numpy_support.vtk_to_numpy(vtk_points.GetData())
landmark_points_array.shape

(5, 3)

In [22]:
rough_vtk_points = numpy_support.numpy_to_vtk(landmark_points_array)
rough_vtk_points.SetName("NoisyPoints")
rough_poly = vtk.vtkPolyData()
rough_poly.SetPoints(vtk.vtkPoints())
rough_poly.GetPoints().SetData(rough_vtk_points)

transform_rough_points_vtk = apply_transformation_and_save(rough_poly, t_gold, save_path, "rough.vtk")
rough_points = numpy_support.vtk_to_numpy(transform_rough_points_vtk.GetPoints().GetData())

Transformed data saved to ./rough.vtk


In [23]:
fine_poly_data = read_vtk_file(fine_points_path)
fine_vtk_points = fine_poly_data.GetPoints()
fine_points_list = numpy_support.vtk_to_numpy(fine_vtk_points.GetData())
fine_points_list.shape

(27, 3)

In [24]:
fine_vtk_points = numpy_support.numpy_to_vtk(fine_points_list)
fine_vtk_points.SetName("NoisyPoints")
fine_poly = vtk.vtkPolyData()
fine_poly.SetPoints(vtk.vtkPoints())
fine_poly.GetPoints().SetData(fine_vtk_points)

transform_fine_points_vtk = apply_transformation_and_save(fine_poly, t_gold, save_path, "rough.vtk")
fine_points = numpy_support.vtk_to_numpy(transform_fine_points_vtk.GetPoints().GetData())


Transformed data saved to ./rough.vtk


In [25]:
source_arr = np.vstack((rough_points, fine_points))
source_arr.shape

(32, 3)

In [35]:
icp2 = vtkIterativeClosestPointTransform()
target = model_vtk
source = numpy_points_to_vtk_polydata(source_arr)

In [36]:
icp2.SetSource(source)
icp2.SetTarget(target)
icp2.GetLandmarkTransform().SetModeToRigidBody()
icp2.DebugOn()
icp2.SetMaximumNumberOfIterations(50)
icp2.SetMaximumNumberOfLandmarks(100)
icp2.CheckMeanDistanceOn()
icp2.SetMaximumMeanDistance(0.1)
icp2.Modified()
icp2.Update()
m = icp2.GetMatrix()
# print("=============",icp2.GetCheckMeanDistance())
# print(icp2.GetLandmarkTransform())
print(m)
# print(icp2)
# print(icp2.GetNumberOfIterations())
# print(icp2.GetInverse())



vtkMatrix4x4 (0x3767d60)
  Debug: Off
  Modified Time: 34212
  Reference Count: 2
  Registered Events: (none)
  Elements:
    0.999998 0.000201737 -0.00174453 0.259901 
    -0.000199701 0.999999 0.00116721 -0.175574 
    0.00174476 -0.00116686 0.999998 -0.0668585 
    0 0 0 1 




### point to point